# HOLA AMIGOS

In [28]:
% reset
from helpers import *
import os
import nltk
import re
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet
import pathlib
from multiprocessing import Process,Lock,Value

def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN
    
    
def dir_size(src_dir):
    print(src_dir)
    return len([name for name in os.listdir(os.fsencode(src_dir))])


def write_clean_docs(src_dir,start,end,lock,p_num=-1,total_files=100,cleaned_files=None):
    
    directory = os.fsencode(src_dir)
    target_dir = src_dir.split('/')[0]+'_clean/'+'/'.join(src_dir.split('/')[1:])
    pathlib.Path(target_dir).mkdir(parents=True, exist_ok=True)
    
    for file in os.listdir(directory):
        filename = os.fsdecode(file)
        if( start <= int(filename.split('_')[0]) <= end):
            with open(os.path.join(src_dir,filename),'r') as f:
                current_doc = f.read()
            with open(os.path.join(target_dir,filename),'w') as f:
                f.write(clean_doc(current_doc))
                
            lock.acquire()
            cleaned_files.value += 1
            print(f'{p_num} | {src_dir}: progress => {cleaned_files.value}/{total_files} ')
            lock.release()

def clean_doc(doc):
    lemmatizer = WordNetLemmatizer()
    
    clean_doc = re.sub(r'<.+?>|[!"#$%&\'()=*+,-./:;?@\[\]^_`{|}~<>]|[0-9]', ' ', doc)
    clean_doc = ' '.join([word.lower() for word in clean_doc.split()])
    tokens =  [word for word in clean_doc.split() if word not in set(stopwords.words('english'))]
    tagged_tokens = [(pair[0],get_wordnet_pos(pair[1])) for pair in nltk.pos_tag(tokens)]
    clean_doc = ' '.join([ lemmatizer.lemmatize(word,tag) for word,tag in tagged_tokens])
    return clean_doc
    

Once deleted, variables cannot be recovered. Proceed (y/[n])? y


In [29]:
dirs = ['aclImdb/train/pos','aclImdb/train/neg','aclImdb/train/unsup']
procs = []
procs_per_dir = 20
lock = Lock()

for (idx,curr_dir) in enumerate(dirs):
    curr_dir_size = dir_size(curr_dir)
    cleaned_files= Value('cleaned_files', 0)
    for i in range(procs_per_dir):
        start = i*curr_dir_size//procs_per_dir
        end = (i+1)*curr_dir_size//procs_per_dir
        proc = Process(target=write_clean_docs, args=(curr_dir,start,end,lock,(i+1)*(idx+1),curr_dir_size,cleaned_files))
        procs.append(proc)
        proc.start()
for proc in procs:
    proc.join()


aclImdb/train/pos
aclImdb/train/neg
aclImdb/train/unsup
2 | aclImdb/train/pos: progress => 1/12500 
1 | aclImdb/train/pos: progress => 1/12500 
2 | aclImdb/train/pos: progress => 2/12500 
6 | aclImdb/train/pos: progress => 1/12500 
8 | aclImdb/train/neg: progress => 1/12500 
6 | aclImdb/train/pos: progress => 2/12500 
5 | aclImdb/train/pos: progress => 1/12500 
6 | aclImdb/train/unsup: progress => 1/50000 
4 | aclImdb/train/neg: progress => 1/12500 
1 | aclImdb/train/pos: progress => 2/12500 
2 | aclImdb/train/neg: progress => 1/12500 
3 | aclImdb/train/unsup: progress => 1/50000 
4 | aclImdb/train/pos: progress => 1/12500 
6 | aclImdb/train/neg: progress => 1/12500 
12 | aclImdb/train/unsup: progress => 1/50000 
3 | aclImdb/train/pos: progress => 1/12500 
10 | aclImdb/train/neg: progress => 1/12500 
2 | aclImdb/train/neg: progress => 2/12500 
2 | aclImdb/train/pos: progress => 3/12500 
12 | aclImdb/train/neg: progress => 1/12500 
15 | aclImdb/train/unsup: progress => 1/50000 
4 | aclI

6 | aclImdb/train/unsup: progress => 9/50000 
4 | aclImdb/train/neg: progress => 10/12500 
2 | aclImdb/train/neg: progress => 9/12500 
8 | aclImdb/train/neg: progress => 14/12500 
15 | aclImdb/train/unsup: progress => 13/50000 
5 | aclImdb/train/pos: progress => 10/12500 
1 | aclImdb/train/pos: progress => 11/12500 
3 | aclImdb/train/unsup: progress => 14/50000 
12 | aclImdb/train/unsup: progress => 8/50000 
10 | aclImdb/train/neg: progress => 12/12500 
8 | aclImdb/train/neg: progress => 15/12500 
4 | aclImdb/train/pos: progress => 10/12500 
6 | aclImdb/train/neg: progress => 11/12500 
18 | aclImdb/train/unsup: progress => 10/50000 
6 | aclImdb/train/unsup: progress => 10/50000 
2 | aclImdb/train/neg: progress => 10/12500 
12 | aclImdb/train/neg: progress => 11/12500 
2 | aclImdb/train/pos: progress => 12/12500 
3 | aclImdb/train/pos: progress => 11/12500 
10 | aclImdb/train/neg: progress => 13/12500 
4 | aclImdb/train/neg: progress => 11/12500 
6 | aclImdb/train/pos: progress => 14/12

3 | aclImdb/train/unsup: progress => 24/50000 
2 | aclImdb/train/pos: progress => 19/12500 
10 | aclImdb/train/neg: progress => 23/12500 
3 | aclImdb/train/pos: progress => 21/12500 
1 | aclImdb/train/pos: progress => 24/12500 
12 | aclImdb/train/unsup: progress => 19/50000 
2 | aclImdb/train/neg: progress => 22/12500 
6 | aclImdb/train/neg: progress => 18/12500 
4 | aclImdb/train/neg: progress => 20/12500 
3 | aclImdb/train/unsup: progress => 25/50000 
6 | aclImdb/train/pos: progress => 24/12500 
12 | aclImdb/train/unsup: progress => 20/50000 
5 | aclImdb/train/pos: progress => 20/12500 
3 | aclImdb/train/pos: progress => 22/12500 
15 | aclImdb/train/unsup: progress => 24/50000 
12 | aclImdb/train/neg: progress => 20/12500 
2 | aclImdb/train/pos: progress => 20/12500 
10 | aclImdb/train/neg: progress => 24/12500 
8 | aclImdb/train/neg: progress => 28/12500 
18 | aclImdb/train/unsup: progress => 20/50000 
2 | aclImdb/train/neg: progress => 23/12500 
3 | aclImdb/train/unsup: progress =>

3 | aclImdb/train/pos: progress => 33/12500 
15 | aclImdb/train/unsup: progress => 30/50000 
12 | aclImdb/train/unsup: progress => 31/50000 
9 | aclImdb/train/unsup: progress => 25/50000 
6 | aclImdb/train/pos: progress => 33/12500 
4 | aclImdb/train/neg: progress => 32/12500 
4 | aclImdb/train/pos: progress => 28/12500 
6 | aclImdb/train/pos: progress => 34/12500 
9 | aclImdb/train/unsup: progress => 26/50000 
10 | aclImdb/train/neg: progress => 31/12500 
5 | aclImdb/train/pos: progress => 31/12500 
2 | aclImdb/train/pos: progress => 29/12500 
2 | aclImdb/train/neg: progress => 34/12500 
15 | aclImdb/train/unsup: progress => 31/50000 
12 | aclImdb/train/unsup: progress => 32/50000 
6 | aclImdb/train/unsup: progress => 22/50000 
6 | aclImdb/train/neg: progress => 27/12500 
3 | aclImdb/train/unsup: progress => 36/50000 
12 | aclImdb/train/neg: progress => 30/12500 
18 | aclImdb/train/unsup: progress => 30/50000 
8 | aclImdb/train/neg: progress => 41/12500 
10 | aclImdb/train/neg: progre

6 | aclImdb/train/unsup: progress => 33/50000 
8 | aclImdb/train/neg: progress => 50/12500 
6 | aclImdb/train/neg: progress => 35/12500 
2 | aclImdb/train/pos: progress => 39/12500 
4 | aclImdb/train/pos: progress => 40/12500 
6 | aclImdb/train/pos: progress => 42/12500 
1 | aclImdb/train/pos: progress => 41/12500 
12 | aclImdb/train/neg: progress => 39/12500 
4 | aclImdb/train/neg: progress => 44/12500 
6 | aclImdb/train/unsup: progress => 34/50000 
6 | aclImdb/train/neg: progress => 36/12500 
15 | aclImdb/train/unsup: progress => 41/50000 
3 | aclImdb/train/pos: progress => 43/12500 
12 | aclImdb/train/neg: progress => 40/12500 
6 | aclImdb/train/pos: progress => 43/12500 
12 | aclImdb/train/unsup: progress => 39/50000 
3 | aclImdb/train/unsup: progress => 48/50000 
4 | aclImdb/train/neg: progress => 45/12500 
10 | aclImdb/train/neg: progress => 41/12500 
4 | aclImdb/train/pos: progress => 41/12500 
6 | aclImdb/train/neg: progress => 37/12500 
15 | aclImdb/train/unsup: progress => 42

...

12 | aclImdb/train/unsup: progress => 8186/50000 
15 | aclImdb/train/unsup: progress => 8295/50000 
9 | aclImdb/train/unsup: progress => 8169/50000 
18 | aclImdb/train/unsup: progress => 8158/50000 
6 | aclImdb/train/unsup: progress => 8192/50000 
3 | aclImdb/train/unsup: progress => 8271/50000 
12 | aclImdb/train/unsup: progress => 8187/50000 
15 | aclImdb/train/unsup: progress => 8296/50000 
9 | aclImdb/train/unsup: progress => 8170/50000 
18 | aclImdb/train/unsup: progress => 8159/50000 
3 | aclImdb/train/unsup: progress => 8272/50000 
9 | aclImdb/train/unsup: progress => 8171/50000 
18 | aclImdb/train/unsup: progress => 8160/50000 
15 | aclImdb/train/unsup: progress => 8297/50000 
12 | aclImdb/train/unsup: progress => 8188/50000 
18 | aclImdb/train/unsup: progress => 8161/50000 
9 | aclImdb/train/unsup: progress => 8172/50000 
15 | aclImdb/train/unsup: progress => 8298/50000 
3 | aclImdb/train/unsup: progress => 8273/50000 
6 | aclImdb/train/unsup: progress => 8193/50000 
9 | aclIm

9 | aclImdb/train/unsup: progress => 8201/50000 
18 | aclImdb/train/unsup: progress => 8184/50000 
15 | aclImdb/train/unsup: progress => 8323/50000 
12 | aclImdb/train/unsup: progress => 8215/50000 
6 | aclImdb/train/unsup: progress => 8216/50000 
3 | aclImdb/train/unsup: progress => 8298/50000 
9 | aclImdb/train/unsup: progress => 8202/50000 
18 | aclImdb/train/unsup: progress => 8185/50000 
12 | aclImdb/train/unsup: progress => 8216/50000 
15 | aclImdb/train/unsup: progress => 8324/50000 
3 | aclImdb/train/unsup: progress => 8299/50000 
9 | aclImdb/train/unsup: progress => 8203/50000 
12 | aclImdb/train/unsup: progress => 8217/50000 
3 | aclImdb/train/unsup: progress => 8300/50000 
6 | aclImdb/train/unsup: progress => 8217/50000 
9 | aclImdb/train/unsup: progress => 8204/50000 
12 | aclImdb/train/unsup: progress => 8218/50000 
6 | aclImdb/train/unsup: progress => 8218/50000 
12 | aclImdb/train/unsup: progress => 8219/50000 
15 | aclImdb/train/unsup: progress => 8325/50000 
6 | aclImd

9 | aclImdb/train/unsup: progress => 8229/50000 
12 | aclImdb/train/unsup: progress => 8249/50000 
18 | aclImdb/train/unsup: progress => 8212/50000 
3 | aclImdb/train/unsup: progress => 8328/50000 
9 | aclImdb/train/unsup: progress => 8230/50000 
3 | aclImdb/train/unsup: progress => 8329/50000 
12 | aclImdb/train/unsup: progress => 8250/50000 
18 | aclImdb/train/unsup: progress => 8213/50000 
6 | aclImdb/train/unsup: progress => 8250/50000 
9 | aclImdb/train/unsup: progress => 8231/50000 
3 | aclImdb/train/unsup: progress => 8330/50000 
6 | aclImdb/train/unsup: progress => 8251/50000 
12 | aclImdb/train/unsup: progress => 8251/50000 
3 | aclImdb/train/unsup: progress => 8331/50000 
9 | aclImdb/train/unsup: progress => 8232/50000 
12 | aclImdb/train/unsup: progress => 8252/50000 
6 | aclImdb/train/unsup: progress => 8252/50000 
3 | aclImdb/train/unsup: progress => 8332/50000 
18 | aclImdb/train/unsup: progress => 8214/50000 
6 | aclImdb/train/unsup: progress => 8253/50000 
12 | aclImdb/

6 | aclImdb/train/unsup: progress => 8297/50000 
9 | aclImdb/train/unsup: progress => 8265/50000 
12 | aclImdb/train/unsup: progress => 8289/50000 
6 | aclImdb/train/unsup: progress => 8298/50000 
18 | aclImdb/train/unsup: progress => 8248/50000 
6 | aclImdb/train/unsup: progress => 8299/50000 
9 | aclImdb/train/unsup: progress => 8266/50000 
12 | aclImdb/train/unsup: progress => 8290/50000 
12 | aclImdb/train/unsup: progress => 8291/50000 
9 | aclImdb/train/unsup: progress => 8267/50000 
12 | aclImdb/train/unsup: progress => 8292/50000 
9 | aclImdb/train/unsup: progress => 8268/50000 
18 | aclImdb/train/unsup: progress => 8249/50000 
9 | aclImdb/train/unsup: progress => 8269/50000 
18 | aclImdb/train/unsup: progress => 8250/50000 
6 | aclImdb/train/unsup: progress => 8300/50000 
12 | aclImdb/train/unsup: progress => 8293/50000 
9 | aclImdb/train/unsup: progress => 8270/50000 
6 | aclImdb/train/unsup: progress => 8301/50000 
18 | aclImdb/train/unsup: progress => 8251/50000 
12 | aclImd

9 | aclImdb/train/unsup: progress => 8308/50000 
12 | aclImdb/train/unsup: progress => 8332/50000 
18 | aclImdb/train/unsup: progress => 8290/50000 
9 | aclImdb/train/unsup: progress => 8309/50000 
12 | aclImdb/train/unsup: progress => 8333/50000 
18 | aclImdb/train/unsup: progress => 8291/50000 
9 | aclImdb/train/unsup: progress => 8310/50000 
12 | aclImdb/train/unsup: progress => 8334/50000 
18 | aclImdb/train/unsup: progress => 8292/50000 
9 | aclImdb/train/unsup: progress => 8311/50000 
18 | aclImdb/train/unsup: progress => 8293/50000 
9 | aclImdb/train/unsup: progress => 8312/50000 
18 | aclImdb/train/unsup: progress => 8294/50000 
9 | aclImdb/train/unsup: progress => 8313/50000 
18 | aclImdb/train/unsup: progress => 8295/50000 
9 | aclImdb/train/unsup: progress => 8314/50000 
18 | aclImdb/train/unsup: progress => 8296/50000 
9 | aclImdb/train/unsup: progress => 8315/50000 
9 | aclImdb/train/unsup: progress => 8316/50000 
9 | aclImdb/train/unsup: progress => 8317/50000 
18 | aclIm

In [30]:
from pathlib import Path
class MyDocs(object):
    def __init__(self, dirname):
        self.dirname = dirname
 
    def __iter__(self):
        pathlist = Path(self.dirname).glob('**/*')
        for path in pathlist:
            path_in_str = str(path)
            if os.path.isfile(path_in_str):
                f=open(path_in_str)
                yield f.read().split()

Once deleted, variables cannot be recovered. Proceed (y/[n])? n
Nothing done.


In [150]:
from gensim.models import Word2Vec,TfidfModel,Phrases
from gensim.corpora import Dictionary
import gensim

docs = MyDocs('aclImdb_clean')
bigram_transformer = Phrases(docs)
wv_model = Word2Vec(bigram_transformer[docs], size=300, window=5, min_count=100, workers=6)

/home/alyswidan/anaconda3/lib/python3.6/site-packages/gensim/models/phrases.py:494: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


In [151]:
def tf_idf_model(doc_path,model_name=None):
    save = model_name!=None
    docs = MyDocs(doc_path)
    bow_dict = Dictionary(docs)
    corpus = [bow_dict.doc2bow(doc) for doc in docs]
    tf_model = TfidfModel(corpus)
    if save:
        tf_model.save(f'models/{model_name}')
    return corpus,bow_dict,tf_model
        

pos_corpus, pos_dict, pos_tf_model = tf_idf_model('aclImdb_clean/train/sup/pos','pos_tf_model')
neg_corpus, neg_dict, neg_tf_model = tf_idf_model('aclImdb_clean/train/sup/neg','neg_tf_model')


In [152]:
import numpy as np
word = pos_dict[pos_corpus[1][0][0]]
vec =  wv_model.wv[word]
tf_idf = pos_tf_model[pos_corpus[1]][0][1]
# np.array(pos_corpus[9])

In [240]:
from sklearn.metrics.pairwise import cosine_similarity
def doc2vec_factory(bow_dict,tf_model,word2vec):
    def doc2vec(doc_bow):
        doc = np.array([bow_dict.id2token[word_id] for word_id,freq in doc_bow])
        doc_tf_idf = np.array([pair[1] for pair in tf_model[doc_bow] if bow_dict.id2token[pair[0]] in word2vec.wv.vocab])
        vecs = np.array([word2vec.wv[word] for word in doc if word in word2vec.wv.vocab])
        doc_vec = np.sum(doc_tf_idf.reshape(-1,1)*vecs,axis=0)
        return doc_vec.reshape(-1,1)
    return doc2vec


In [241]:
pos_doc2vec = doc2vec_factory(pos_dict,pos_tf_model,wv_model)
neg_doc2vec = doc2vec_factory(neg_dict,neg_tf_model,wv_model)

pos_vecs = []
for corpus in pos_corpus:
    pos_vecs.append(pos_doc2vec(corpus))
pos_vecs = np.array(pos_vecs)




In [242]:
neg_vecs = []
for corpus in neg_corpus:
    neg_vecs.append(neg_doc2vec(corpus))
neg_vecs = np.array(neg_vecs)

In [249]:
neg_vecs = neg_vecs.reshape(-1,300)
pos_vecs = pos_vecs.reshape(-1,300)

In [277]:
X = np.concatenate((pos_vecs,neg_vecs),axis=0)
y = np.asarray([1]*pos_vecs.shape[0] + [-1]*pos_vecs.shape[0])
n_samples = X.shape[0]
idx_perm = np.random.permutation(n_samples)
train_idx = idx_perm[0:int(0.7*n_samples)]
val_idx = idx_perm[int(0.7*n_samples+1):n_samples]
X_train = X[train_idx]
y_train = y[train_idx]
X_val = X[val_idx]
y_val = y[val_idx]

In [286]:
from sklearn.svm import SVC

clf = SVC(C=100)
clf.fit(X_train, y_train)

SVC(C=100, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)

In [287]:
np.mean(clf.predict(X_val) == y_val)

0.79623949859981336

In [284]:
from sklearn.ensemble import RandomForestClassifier
forest = RandomForestClassifier(n_estimators=500,min_samples_split=50,n_jobs=-1)
forest.fit(X_train,y_train)


RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=50,
            min_weight_fraction_leaf=0.0, n_estimators=500, n_jobs=-1,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False)

In [285]:
np.mean(forest.predict(X_val) == y_val)

0.78783837845046001

In [288]:
from sklearn.ensemble import AdaBoostClassifier
ada = AdaBoostClassifier(n_estimators=200)
ada.fit(X_train,y_train)

AdaBoostClassifier(algorithm='SAMME.R', base_estimator=None,
          learning_rate=1.0, n_estimators=200, random_state=None)

In [289]:
np.mean(ada.predict(X_val) == y_val)

0.7889051873583145

In [290]:
from sklearn.ensemble import GradientBoostingClassifier
gboost = GradientBoostingClassifier(n_estimators=300)
gboost.fit(X_train,y_train)

GradientBoostingClassifier(criterion='friedman_mse', init=None,
              learning_rate=0.1, loss='deviance', max_depth=3,
              max_features=None, max_leaf_nodes=None,
              min_impurity_decrease=0.0, min_impurity_split=None,
              min_samples_leaf=1, min_samples_split=2,
              min_weight_fraction_leaf=0.0, n_estimators=300,
              presort='auto', random_state=None, subsample=1.0, verbose=0,
              warm_start=False)

In [291]:
np.mean(gboost.predict(X_val) == y_val)

0.80330710761434854